In [66]:
import pandas as pd
import numpy as np 
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import requests
from bs4 import BeautifulSoup
import plotly.offline as pyo
import plotly.graph_objs as go
import plotly.io as py
import scipy.stats as stats
import statsmodels.api as sm
import pylab
from datetime import datetime

#Display all columns
pd.set_option('display.max_columns', None)
plt.style.use('ggplot')

%matplotlib inline

## Summary of the main features 

|Dataset (site) |Name | Type  | Description   |
| -------- | -------- | -------- | -------- |
|beers.csv||||
|beers (Ba, Rb)|  abv  | Series - float  | Indicates the beer's alcohol by volume (%)|
|beers (Ba, Rb)|  avg  | Series - float  | Average rating given to the beer (averaging scores of different factors for each beer)|
|beers (Ba, Rb)|  avg_computed | Series - float  | ? |
|beers (Ba, Rb)|  avg_matched_valid_ratings | Series - float  | average of valid ratings (from users following certains criteria) |
|beers (Ba)|  ba_score  | Series - float  |Score for the beer advocate (ba) website|
|beers (Ba, Rb)|  beer_id  | Series - int  | Unique ID of each beer|
|beers (Ba, Rb)|  beer_name  | Series - string  | Name of the beer |
|beers (Ba, Rb)|  beer_wout_brewery_name  | Series - string  | name of the beer without the brewery name in it|
|beers (Ba, Rb)|  brewery_id  | Series - int  | Unique ID for each brewery the beers belong to|
|beers (Ba, Rb)|  brewery_name  | Series - string  | Name of the brewery|
|beers (Ba)|  bros_score  | Series - int  | score given by admins of the website |
|beers (Ba, Rb)|  nbr_matched_valid_ratings  | Series - int | number of valid ratings for this beer (rating/user follows certain criteria)|
|beers (Ba, Rb)|  nbr_ratings  | Series - int | total amount of ratigns for this beer |
|beers (Ba, Rb)|  nrb_reviews  | Series - int  | total number of text reviews for this beer|
|beers (Ba, Rb)| style |Series - string| style of beer (e.g. pale ale, irish dry stout...)|
|beers (Ba, Rb)| z_score |Series - float| standardized rating for this beer |
|beers (Rb)| overall_score | Series - float| average of the beer's overall rating given by the users|
|beers (Rb)| style_score | Series - float | average rating for beers of this style|
|beers| diff | Series - flaot| difference in score between Rb and Ba for this beer (between 0 and 1)|
|beers| sim | Series - float| similarity in score between Rb and Ba for this beer (between 0 and 1)|
| breweries.csv |  |  |  |
|breweries (Ba, Rb)| id |Series - int| unique ID for each brewery|
|breweries (Ba, Rb)| location |Series - string| full name of the state (USA) or country of origin of the brewery |
|breweries (Ba, Rb)| name |Series - string| full name of the brewery |
|breweries (Ba, Rb)| nbr_beers |Series - int| number of different beers brewed in this brewery|
| users.csv |  |  |  |
| users (Ba, Rb) | joined | Series - int | Unix timestamp for when the user joined the website |
| users (Ba, Rb) | location | Series - string | full name of the state (USA) or country of the user |
| users (Ba, Rb) | nbr_ratings | Series - int | total number of ratings given by the user |
| users (Ba, Rb) | nbr_reviews | Series - int | total number of rewviews given by the user |
| users (Ba, Rb) | user_id | Series - string | unique user ID in the format: username.ID |
| users (Ba, Rb) | user_name | Series - string | username |
| users (Ba, Rb) | user_name_lowercase | Series - string | username in lower case |

## Data preprocessing:

### Importing new datasets and cleaning them 

In [67]:
#wikipedia dataset for states (US) superficies
wiki_url_4usa = 'https://en.wikipedia.org/wiki/List_of_U.S._states_and_territories_by_area'
#Get the html of the pages
response_us = requests.get(wiki_url_4usa)
soup_us = BeautifulSoup(response_us.text,'lxml')

#Find the useful table from in the html and convert it into pandas df 
superficies_list_us = soup_us.find('table', attrs={'class':"wikitable"})
df_superficies_us = pd.read_html(str(superficies_list_us))[0]

#Clean the datafram
df_superficies_us = df_superficies_us[['State / territory', 'Total km2']] #Keep only the columns we need
df_superficies_us = df_superficies_us.rename(columns={'State / territory': 'location', 'Total km2' : 'km2'}) #rename the column
df_superficies_us['location'] = 'United States, ' + df_superficies_us['location'] #add the country name to be consistent with the other dataset
df_superficies_us = df_superficies_us[:-3] #remove the last 3 rows (not states)
df_superficies_us['km2'] = df_superficies_us['km2'].astype(float) #convert the km2 column to float

#_______________________________________________________________________________________________________________________

#wikipedia dataset for country superficies
wiki_url = 'https://en.wikipedia.org/wiki/List_of_countries_and_dependencies_by_area'

#Get the html of the pages
response = requests.get(wiki_url)
soup = BeautifulSoup(response.text,'lxml')

#Find the useful table from in the html and convert it into pandas df 
superficies_list = soup.find('table',attrs={'class':"wikitable"})
df_superficies = pd.read_html(str(superficies_list))[0]


#Keep only the columns we need and clean them
df_superficies = df_superficies[['Country / dependency', 'Total in km2 (mi2)']]
df_superficies.rename(columns={'Country / dependency':'location', 'Total in km2 (mi2)':'km2'}, inplace=True) #rename the columns
df_superficies['km2'] = df_superficies['km2'].str.replace(',', '') #remove the comma
df_superficies['km2'] = df_superficies['km2'].str.split(' ').str[0]  #remove the text in parenthesis (mi2)
df_superficies['location'] = df_superficies['location'].str.replace(r'\s*\([^)]*\)', '', regex=True)  #Remove all parenthesis and text inside in the location (ex : remove (China) in 'Hong Kong (China)')
df_superficies['km2'] = df_superficies['km2'].astype(float) #convert the km2 column to int

#Change the name of the countries to be consistent with the other dataset
df_superficies.location = df_superficies.location.replace({'Slovakia' : 'Slovak Republic', 'North Macedonia' : 'Macedonia', 'Trinidad and Tobago' : 'Trinidad & Tobago'})

#________________________________________________________________

#Dataset for UK coutries superficies to be consistent with the other dataset (breweries and beers)
df_superficies_uk = pd.DataFrame({'location': ['England', 'Scotland', 'Wales', 'Northern Ireland'], 
                                  'km2': [130279, 78772, 20779, 14130]}) #create the dataframe (small so easy to do it manually)

#_______________________________________________________________________________________________________________________

#Concatenate the two first dataframe 
df_superficies_temp = pd.concat([df_superficies, df_superficies_us]) #concatenate the two dataframe

#Merging the dataframes with the UK dataframe
df_superficies_tot = pd.concat([df_superficies_temp, df_superficies_uk])


C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\2810214126.py:9: FutureWarning:

Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.

C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\2810214126.py:29: FutureWarning:

Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.



In [68]:
#Wikipedia datasets for the population of the countries
wiki_url_pop = "https://en.wikipedia.org/wiki/List_of_countries_and_dependencies_by_population"

#Get the html of the pages
response_pop = requests.get(wiki_url_pop)
soup_pop = BeautifulSoup(response_pop.text,'lxml')

#Find the useful table from in the html and convert it into pandas df 
population = soup_pop.find("table", attrs={"class": "wikitable"})
df_population = pd.read_html(str(population))[0]
df_population = df_population[['Country / Dependency', 'Population']] #Keep only the columns we need
df_population.rename(columns = {'Country / Dependency' : 'location', 'Population' : 'population'}, inplace=True) #rename the columns

#Change the name of the countries to be consistent with the other dataset
df_population.location = df_population.location.replace({'Slovakia' : 'Slovak Republic', 
                                                           'North Macedonia' : 'Macedonia', 
                                                           'Trinidad and Tobago' : 'Trinidad & Tobago', 
                                                           'Puerto Rico (US)' : 'Puerto Rico',
                                                           'Jersey (UK)' : 'Jersey', 
                                                           'Faroe Islands (Denmark)' : 'Faroe Islands'})


#_______________________________________________________________________________________________________________________

#Wikipedia dataset for the population of the US states
wiki_url_pop_US = "https://simple.wikipedia.org/wiki/List_of_U.S._states_by_population"

#Get the html of the pages
response_pop_US = requests.get(wiki_url_pop_US)
soup_pop_US = BeautifulSoup(response_pop_US.text,'lxml')

#Find the useful table from in the html and convert it into pandas df
population_US = soup_pop_US.find("table", attrs={"class": "wikitable"})
df_population_US = pd.read_html(str(population_US))[0]
df_population_US = df_population_US[['State', 'Census population, April 1, 2020 [1][2]']] #Keep only the columns we need
df_population_US.rename(columns={'State' : 'location', 'Census population, April 1, 2020 [1][2]' : 'population'}, inplace = True)
df_population_US['location'] = 'United States, ' + df_population_US['location'] #add the country name to be consistent with the other dataset
df_population_US = df_population_US[:-4] #remove the last 4 rows (not states)

#_______________________________________________________________________________________________________________________

#Wikipedia dataset for the population of the UK countries

df_population_UK = pd.DataFrame({'location': ['England', 'Scotland', 'Wales', 'Northern Ireland'], 
                                 'population' : [56550138, 5463300, 3152879, 1893667]}) #create the dataframe (small so easy to do it manually)


#_______________________________________________________________________________________________________________________

# Concatenate the two first dataframe 
df_population_tot = pd.concat([df_population, df_population_US]) #concatenate the two dataframe

# Concatenate the previous df with the one from UK and reset index
df_population_tot = pd.concat([df_population_tot, df_population_UK])
df_population_tot.reset_index(drop=True, inplace=True)



C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\2783564457.py:10: FutureWarning:

Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.

C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\2783564457.py:34: FutureWarning:

Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.



### Matched websites 

#### Loading the data

In [69]:
#RateBeer and Beer Advocate matched website data :

df_beer = pd.read_csv("matched_beer_data/beers.csv", header=1)
df_breweries  = pd.read_csv("matched_beer_data/breweries.csv", header=1)
df_users = pd.read_csv("matched_beer_data/users.csv", header=1)
df_rating = pd.read_csv("matched_beer_data/ratings.csv", header=1)
df_users_approx = pd.read_csv("matched_beer_data/users_approx.csv", header=1)

#### Merging, cleaning and visualize the matched datasets (beers and breweries)

In [70]:
#Merge the two dataframes on the brewery_id column with respect to the beers to have access to the location of every beer
df_beer_breweries = pd.merge(df_beer, df_breweries, left_on='brewery_id', right_on='id', how='left')

#Clean the dataframe by dropping the columns that are not useful for the analysis
df_beer_breweries_clean = df_beer_breweries.drop(['beer_wout_brewery_name', 'beer_wout_brewery_name.1', 'style','abv.1', 'id', 'id.1', 'name', 'name.1', 'beer_name.1', 'brewery_name.1', 'location.1', 'nbr_beers.1'], axis=1)


#Choose to keep style from RateBeer and drop the style from Beer Advocate (the style from Beer Advocate is too precise)
df_beer_breweries_clean.rename(columns={'style.1':'style'}, inplace=True)

#In the data set, the features with .1 at the end are the ones from Beer Advocate and the ones without .1 are the ones from RateBeer

#### Merging and cleaning the matched datasets (superficies and breweries)

In [71]:
#Merge the dataframe with the superficies dataframe to have access to the superficies of every beer
df_breweries_superficies = pd.merge(df_breweries, df_superficies_tot, on='location', how='left')

#Drop row with NaN values in km2 column
df_breweries_superficies = df_breweries_superficies.dropna(subset=['km2'])

#Drop the location with less than 5 breweries (to do a beer trip, we need to have different breweries to visit!)
df_breweries_superficies_flt = df_breweries_superficies.groupby('location').filter(lambda x: len(x) >= 5)

#In the data set, the features with .1 at the end are the ones from Beer Advocate and the ones without .1 are the ones from RateBeer

#### Merging and cleaning the dataset about users

We need to merge it with the dataframe imported from Wikipedia with the population of the locations, because the goal of this preprocessing is to express finally the places where there are the biggest amount of reviewer per capita. 

In [72]:
#Selection of the columns to keep and rename them
df_users_approx_flt = df_users_approx[['location', 'user_id', 'user_name', 'nbr_ratings', 'nbr_ratings.1']]
df_users_approx_flt = df_users_approx_flt.rename(columns={'nbr_ratings':'nbr_ratings_beer_advocate', 'nbr_ratings.1':'nbr_ratings_ratebeer'})


#Check that every user has at least one rating in each website (insure that the user is active)
df_users_approx_flt = df_users_approx_flt.drop(df_users_approx_flt[(df_users_approx_flt['nbr_ratings_beer_advocate'] == 0) | (df_users_approx_flt['nbr_ratings_ratebeer'] == 0)].index)  # Drop rows where there is no ratings in one of the two websites

#Merge the dataframe with the population dataframe to have access to the population of every country
df_users_pop = pd.merge(df_users_approx_flt, df_population_tot, on='location', how='left')


### RateBeer Website

#### Loading the data

In [73]:
#RateBeer website data :

df_beer_RB = pd.read_csv("RateBeer/beers.csv")
df_breweries_RB  = pd.read_csv("RateBeer/breweries.csv")
df_users_RB = pd.read_csv("RateBeer/users.csv")
df_beer_ratings_RB = pd.read_csv("RateBeer/ratings_TTRB.csv")

#Remove rows with NaN values
df_beer_RB= df_beer_RB.dropna(subset=["zscore"])


#### Set threshold to clean the beers and users data

In [74]:
# Set a threshold (95%) for the number of ratings
ratings_threshold95 = df_beer_RB['nbr_ratings'].quantile(0.95)

# Filter beers based on the threshold
filtered_beers95 = df_beer_RB[df_beer_RB['nbr_ratings'] >= ratings_threshold95]

# Set a threshold (99%) for the number of ratings
ratings_threshold99 = df_beer_RB['nbr_ratings'].quantile(0.99)

# Filter beers based on the threshold
filtered_beers99 = df_beer_RB[df_beer_RB['nbr_ratings'] >= ratings_threshold99]

# Create the new dataframe with the filtered beers
df_filtered_beer_RB = filtered_beers95

# Set a threshold (99%) for the number of ratings per users 
ratings_threshold99 = df_users_RB['nbr_ratings'].quantile(0.99)

# Filter beers based on the threshold
filtered_users99 = df_users_RB[df_users_RB['nbr_ratings'] >= ratings_threshold99]

# Create the new dataframe with the filtered users
df_filtered_users_RB = filtered_users99

# In df_beer_ratings_RB we only keep the users in the 99% threshold 
df_beer_ratings_RB_filter_on_users = df_beer_ratings_RB[df_beer_ratings_RB['user_id'].isin(df_filtered_users_RB['user_id'])]

# In df_beer_ratings_RB_filter_on_users we only keep the beers in the 95% threshold 
df_beer_ratings_RB_filtered_on_users_and_beers = df_beer_ratings_RB_filter_on_users[df_beer_ratings_RB_filter_on_users['beer_id'].isin(df_filtered_beer_RB['beer_id'])]


#### Filter on z-score and rank by ascending order

In [75]:
#Filter the beers from RateBeer based on their zscore
df_filtered_beer_RB_sorted = df_filtered_beer_RB.sort_values(by='zscore', ascending=False)

#Keep only the columns we need
df_filtered_beer_RB_sorted = df_filtered_beer_RB_sorted.loc[:, ['beer_id', 'beer_name', 'brewery_id', 'brewery_name', 'avg', 'overall_score', 'zscore']]

# Filter the sorted dataframe based on the 'beer_id' column using the filtered beer ratings and user activity dataframes
df_filtered_beer_RB_sorted = df_filtered_beer_RB_sorted[df_filtered_beer_RB_sorted['beer_id'].isin(df_beer_ratings_RB_filtered_on_users_and_beers['beer_id'])]

#Drop the beers with a negative zscore
df_filtered_beer_RB_zscore_sorted = df_filtered_beer_RB_sorted.drop(df_filtered_beer_RB_sorted[df_filtered_beer_RB_sorted['zscore'] < 0].index)
df_filtered_beer_RB_zscore_sorted = pd.DataFrame(df_filtered_beer_RB_zscore_sorted)

### BeerAdvocate website

#### Loading the data

In [76]:
#RateBeer website data :
df_beer_BA = pd.read_csv("BeerAdvocate/beers.csv")
df_breweries_BA  = pd.read_csv("BeerAdvocate/breweries.csv")
df_users_BA = pd.read_csv("BEerAdvocate/users.csv")
df_beer_ratings_BA = pd.read_csv("BeerAdvocate/ratings_TTBA.csv")

#Remove rows with NaN values
df_beer_BA= df_beer_BA.dropna(subset=["zscore"])

#### Set threshold to clean the beers and users data

In [77]:
# Set a threshold (95%) for the number of ratings
ratings_threshold95_BA = df_beer_BA['nbr_ratings'].quantile(0.95)

# Filter beers based on the threshold
filtered_beers95_BA = df_beer_BA[df_beer_BA['nbr_ratings'] >= ratings_threshold95_BA]

# Set a threshold (99%) for the number of ratings
ratings_threshold99_BA = df_beer_BA['nbr_ratings'].quantile(0.99)

# Filter beers based on the threshold
filtered_beers99_BA = df_beer_BA[df_beer_BA['nbr_ratings'] >= ratings_threshold99_BA]

# Create the new dataframe with the filtered beers
df_filtered_beer_BA = filtered_beers95_BA

# Set a threshold (99%) for the number of ratings per users 
ratings_threshold99_BA = df_users_BA['nbr_ratings'].quantile(0.99)

# Filter beers based on the threshold
filtered_users99_BA = df_users_BA[df_users_BA['nbr_ratings'] >= ratings_threshold99_BA]

# Create the new dataframe with the filtered users
df_filtered_users_BA = filtered_users99_BA

# In df_beer_ratings_BA we only keep the users in the 99% threshold 
df_beer_ratings_BA_filter_on_users = df_beer_ratings_BA[df_beer_ratings_BA['user_id'].isin(df_filtered_users_BA['user_id'])]

# In df_beer_ratings_BA we only keep the beers in the 95% threshold 
df_beer_ratings_BA_filtered_on_users_and_beers = df_beer_ratings_BA_filter_on_users[df_beer_ratings_BA_filter_on_users['beer_id'].isin(df_filtered_beer_BA['beer_id'])]

#### Filter on z-score and rank by ascending order

In [78]:
#Filter the beers from Beer Advocate based on their zscore
df_filtered_beer_BA_sorted = df_filtered_beer_BA.sort_values(by='zscore', ascending=False)

#Keep only the columns we need
df_filtered_beer_BA_sorted = df_filtered_beer_BA_sorted.loc[:, ['beer_id', 'beer_name', 'brewery_id', 'brewery_name', 'avg', 'ba_score', 'bros_score', 'zscore']]

# Filter the sorted dataframe based on the 'beer_id' column using the filtered beer ratings and user activity dataframes
df_filtered_beer_BA_sorted = df_filtered_beer_BA_sorted[df_filtered_beer_BA_sorted['beer_id'].isin(df_beer_ratings_BA_filtered_on_users_and_beers['beer_id'])]

#Drop the beers with a negative zscore and create a new dataframe
df_filtered_beer_BA_zscore_sorted = df_filtered_beer_BA_sorted.drop(df_filtered_beer_BA_sorted[df_filtered_beer_BA_sorted['zscore'] < 0].index)
df_filtered_beer_BA_zscore_sorted = pd.DataFrame(df_filtered_beer_BA_zscore_sorted)

#### Analysis of distribution the data from the different websites 

In [79]:
#Plotting the ccdf of the zscore for both websites

ccdf = px.scatter(df_filtered_beer_BA ,x='zscore', y=df_filtered_beer_BA['zscore'].rank(pct=True), labels={'x': 'zscore', 'y': 'CCDF'})

#Adding legend
ccdf['data'][0]['showlegend']=True
ccdf['data'][0]['name']='BeerAdvocate'

ccdf.add_scatter(x=df_filtered_beer_RB['zscore'], y=df_filtered_beer_RB['zscore'].rank(pct=True),
                mode='markers', name='RateBeer')

ccdf.show()
# Export html file for the website 
pyo.plot(ccdf, filename='intro_ccdf_comparaison.html', auto_open=False)


'intro_ccdf_comparaison.html'

This plot shows the CDF of each website. By simply looking at it, we can make the hypothesis that BeerAdvocate users tend to give higher z_score than RateBeer users. We will test this hypothesis later on.

In [80]:
# Plot the z-score for each beer in function of the number of ratings
fig_zscore_vs_nbr_ratings_BA = px.scatter(filtered_beers99_BA, x='zscore', y='nbr_ratings', color='zscore')
#fig_zscore_vs_nbr_ratings_BA.update_layout(title='Z-Score vs Number of Ratings') #----> we remove the title because it's nicer to add them directly in the website
fig_zscore_vs_nbr_ratings_BA.update_traces(showlegend=False)
fig_zscore_vs_nbr_ratings_BA.show()

#Save the plot in html format
pyo.plot(fig_zscore_vs_nbr_ratings_BA, filename='intro_zscore_vs_nbr_ratings_BA_99.html', auto_open=False)

'intro_zscore_vs_nbr_ratings_BA_99.html'

In [81]:
# Plot the z-score for each beer in function of the number of ratings
fig_zscore_vs_nbr_ratings_RB = px.scatter(filtered_beers99, x='zscore', y='nbr_ratings', color='zscore')

#fig_zscore_vs_nbr_ratings_RB.update_layout(title='Z-Score vs Number of Ratings') #----> we remove the title because it's nicer to add them directly in the website
fig_zscore_vs_nbr_ratings_RB.update_traces(showlegend=False)
fig_zscore_vs_nbr_ratings_RB.show()

#Save the plot in html format
pyo.plot(fig_zscore_vs_nbr_ratings_RB, filename='intro_zscore_vs_nbr_ratings_RB_99.html', auto_open=False)

'intro_zscore_vs_nbr_ratings_RB_99.html'

These two plots give us a way to visualize the zscore distribution of the 1% of the most reviewed beers from both sites. It also gives us an idea of the number of times that the most-rated beers are reviewed.

After graphing the data and analyzing it a little in the previous graphs, certain hypotheses need to be tested so that they can be used correctly in the future. Indeed we are trying different tests to see if the z_score distribution of the beers from the two websites are directly comparable.

In [82]:
#permutation test

def permutation_test(dataset1, dataset2, num_permutations=1000):
    observed_diff = np.abs(np.mean(dataset1) - np.mean(dataset2))

    # Combine the samples
    combined_data = np.concatenate([dataset1, dataset2])

    # Initialize an array to store permuted differences
    permuted_diffs = np.zeros(num_permutations)

    for i in range(num_permutations):
        np.random.shuffle(combined_data)
        permuted_diffs[i] = np.abs(np.mean(combined_data[:len(dataset1)]) - np.mean(combined_data[len(dataset1):]))

    # Calculate the p-value
    p_value_permutation = np.mean(permuted_diffs >= observed_diff)

    return p_value_permutation

# Perform permutation test
p_value_permutation = permutation_test(df_filtered_beer_BA['zscore'], df_filtered_beer_RB['zscore'])
print(f"Permutation Test P-value: {p_value_permutation}")


Permutation Test P-value: 0.0


In [83]:
#Kolmogorov-Smirnov Test

statistic, p_value = stats.ks_2samp(df_filtered_beer_BA['zscore'], df_filtered_beer_RB['zscore'])
print(f"KS Statistic: {statistic}, P-value: {p_value}")

KS Statistic: 0.1631406099787727, P-value: 1.1596746240507313e-24


The ccdf plot gave us the intuition that the z_score distribution of the beers from the two websites is not directly comparable. We tried to confirm this intuition by doing two different hypothesis tests that we thought were well suited to test our hypothesis. We first computed a permutation test which randomly shuffled the data from the two different datasets and evaluate if the difference of z_score distribution is significant. The test gave us a p-value of 0.0 which confirms our initial intuition that there is a significant difference between the two distributions. To be sure, we also tried to do a Kolmogorov-Smirnov test which gave us a p-value of 1.16e-24 which also confirmed our intuition.


In [84]:
#Add a column with the date in datetime format
datetime_date_BA=pd.to_datetime(df_beer_ratings_BA['date'], unit='s')
df_beer_ratings_BA_date=df_beer_ratings_BA
df_beer_ratings_BA_date['date_datetime']=datetime_date_BA

datetime_date_RB=pd.to_datetime(df_beer_ratings_RB['date'], unit='s')
df_beer_ratings_RB_date=df_beer_ratings_RB
df_beer_ratings_RB_date['date_datetime']=datetime_date_RB


In [106]:
from IPython.display import display
from plotly.offline import init_notebook_mode, iplot

init_notebook_mode(connected=True)

# Group the dataframes by year and count the number of reviews in each year
reviews_by_year_BA = df_beer_ratings_BA_date.groupby(df_beer_ratings_BA_date['date_datetime'].dt.year).size().reset_index(name='total_reviews_by_year')

reviews_by_year_RB = df_beer_ratings_RB_date.groupby(df_beer_ratings_RB_date['date_datetime'].dt.year).size().reset_index(name='total_reviews_by_year')

# plotting BeerAdvocate bar plot
fig_review_per_year = px.bar(reviews_by_year_BA, x='date_datetime', y='total_reviews_by_year',
             labels={'date_datetime': 'Year', 'total_reviews_by_year': 'Total Number of Reviews'})

# addding RateBeer bar plot
fig_review_per_year.add_trace(go.Bar(x=reviews_by_year_RB['date_datetime'],
                     y=reviews_by_year_RB['total_reviews_by_year'],
                     name='RateBeer'))
#adding legend
fig_review_per_year['data'][0]['showlegend']=True
fig_review_per_year['data'][0]['name']='BeerAdvocate'
fig_review_per_year.update_layout(barmode='group')
fig_review_per_year.show()

#Save the plot in html format
pyo.plot(fig_review_per_year, filename='intro_review_per_year.html', auto_open=False)

'intro_review_per_year.html'

This plot show the difference of the number of review year by year of the two website. We can see that while the number of review of both sites is increasing before 2014-2015, BeerAdvocate tend to grow faster than (or has more active user) than RateBeer. We can also observe that both site decrease in number of review after 2015. The number of reviews in 2017 for both site is particularly low, this could be due to the fact that the dataset may have been collected during 2017 and that the number of review of 2017 is not complete.

In [86]:
# Filter BA and RB beer dataframes keeping only the beers that are in matched beer dataset
BA_data = df_beer_BA[df_beer_BA['beer_id'].isin(df_beer['beer_id'])]
RB_data = df_beer_RB[df_beer_RB['beer_id'].isin(df_beer['beer_id.1'])]
unique_beers_BA = BA_data['beer_id'].nunique()
unique_beers_RB = RB_data['beer_id'].nunique()
unique_beers_matched = df_beer['beer_id'].nunique()

# Calculate the proportions for both sites
proportion_BA = unique_beers_BA / unique_beers_matched
proportion_RB = unique_beers_RB / unique_beers_matched

# Convert proportions to percentage
proportion_BA_percentage = proportion_BA * 100
proportion_RB_percentage = proportion_RB * 100

# Create a dataframe for the proportions
data = {'Website': ['BeerAdvocate', 'RateBeer'], 'Proportion': [proportion_BA_percentage, proportion_RB_percentage]}
df_proportion = pd.DataFrame(data)

# Create the bar plot
fig_proportion = px.bar(df_proportion, x='Website', y='Proportion', labels={'Website': 'Website', 'Proportion': 'Proportion of Unique Beers (%)'})

# Show the plot
fig_proportion.show()

pyo.plot(fig_proportion, filename='fig_intro_proportion.html',auto_open=False)

'fig_intro_proportion.html'

This plot shows the proportion of beer present on both websites versus the proportion of beer present on only one of the two websites. We can see that the majority of the beer is present on both websites, which allows us to work directly with matched files without "losing" too much data.

## Start to build our different trips

**DISCOVERY TRIP**

In [87]:
#Determine the rarest beer style in the dataset
grouped = df_beer_breweries_clean.groupby('style').count()
grouped.sort_values(by='beer_id', ascending=True, inplace=True)
style_rare = grouped.head(15)

#Keep only the 20 rarest beer style in the dataset
df_beer_breweries_rare = df_beer_breweries_clean[df_beer_breweries_clean['style'].isin(style_rare.index)]

#Drop the locations where there is less than 5 beers of the rarest style
df_beer_breweries_rare_flt = df_beer_breweries_rare.groupby('location').filter(lambda x: len(x) >= 5)

#Sort the df showing the location with the bigger amount of rare beers
pre_list_sorted = df_beer_breweries_rare_flt.groupby('location').count().sort_values(by='beer_id', ascending=False)

#Add a column with the number of rare beers per location
pre_list_sorted['count'] = df_beer_breweries_rare_flt.groupby('location').count().sort_values(by='beer_id', ascending=False).beer_id

#Create a list of the top 10 countries with the most rare beers, but we restrein the list to 2 location from the US
count_us=0
top_10_discov = []
for location in pre_list_sorted.index:
    if  "United States" in location and count_us < 2: 
        top_10_discov.append(location)
        count_us+=1
    elif "United States" not in location:
        top_10_discov.append(location)

    if len(top_10_discov) == 10:
        break

#Create a dataframe with the top 10 countries with the most rare beers for ploting 
df_top_10_discov = pre_list_sorted[pre_list_sorted.index.isin(top_10_discov)]
df_top_10_discov.reset_index(inplace=True)

#Plot the top 10 countries with the most rare beers, using plotly
fig_top10_discov = px.bar(df_top_10_discov, x='location', y='beer_id', color=df_top_10_discov.index)
#fig_top10_discov.update_layout(title='Locations with the bigger amount of rare beers') #----> we remove the title because it's nicer to add them directly in the website
fig_top10_discov.update_yaxes(title='Number of rare beers')
fig_top10_discov.update_xaxes(title='Location')
fig_top10_discov.update_layout(showlegend=False)
fig_top10_discov.show()

# Export html file for the website 
pyo.plot(fig_top10_discov, filename='top10_discov.html', auto_open=False)

'top10_discov.html'

In this ranking, we can see the locations that are the most innovative for beer creation. Brewers in these regions like to try out new types of beer and don't do the classic. You should definitely go there if you want to satisfy your curiosity and expand your knowledge!

**BREWERIES PER KM2**

In [88]:
#Group the breweries by country, count the number of breweries and divide by the superfices of the location to have a density :
df_breweries_superficies_count = df_breweries_superficies_flt.groupby(['location']).id.count()

#display(df_breweries_superficies_flt)

#Get the values of the km2 in every location 
df_breweries_superficies_km2 = df_breweries_superficies_flt.groupby(['location']).km2.mean()

#Concatenate the two dataframe to have access to the density of breweries per km2
df_density = pd.concat([df_breweries_superficies_count, df_breweries_superficies_km2], axis=1)

#Compute the density of breweries per km2
df_density['density'] = df_density['id'] / df_density['km2']

#Rename the columns and sort the dataframe by density
df_density.rename(columns={'id':'nbr_breweries'}, inplace=True)
df_density.reset_index(inplace=True)
df_density.sort_values(by=['density'], ascending=False, inplace=True) 

#Create a list of the top 10 countries with the most rare beers, but we restrein the list to 2 location from the US
count=0
top_ten_density = []
for location in df_density.location:
    if  "United States" in location and count < 2: 
        top_ten_density.append(location)
        count+=1
    elif "United States" not in location:
        top_ten_density.append(location)

    if len(top_ten_density) == 10:
        break


#Create a dataframe with the top 10 countries with the most rare beers for ploting 
df_top_ten_density = df_density[df_density.location.isin(top_ten_density)]

#Plot with superficies vs number of breweries using plotly
fig_superficie_vs_nbr_breweries = px.scatter(df_density, x='nbr_breweries', y='km2', color='location')
#fig_superficie_vs_nbr_breweries.update_layout(title='Superficies of the countries vs number of breweries') #----> we remove the title because it's nicer to add them directly in the website
fig_superficie_vs_nbr_breweries.update_traces(showlegend=False)
fig_superficie_vs_nbr_breweries.show()


#Plot the density of breweries per km2 using plotly
fig_top10_density_breweries = px.bar(df_top_ten_density, x='location', y='density', color='location')
#fig_top10_density_breweries.update_layout(title='Density of breweries per km2') #----> we remove the title because it's nicer to add them directly in the website
fig_top10_density_breweries.update_yaxes(title='Density of breweries per km2')
fig_top10_density_breweries.update_xaxes(title='Location')
fig_top10_density_breweries.update_layout(showlegend=False)
fig_top10_density_breweries.show()

# Export html file for the website 
pyo.plot(fig_superficie_vs_nbr_breweries, filename='superficie_vs_nbr_breweries.html', auto_open=False)
pyo.plot(fig_top10_density_breweries, filename='top10_density_breweries.html', auto_open=False)


'top10_density_breweries.html'

The first graph shows the superficies and the number of breweries in every locations. We can see that most of the locations are small and don't have a lot of breweries (which makes totally sense). However, some stand out in particular: either they have many breweries and are small (interesting for this trip), or they are very large and don't have many breweries (not relevant here).

The ranking result on the second graph summarises the most interesting found in the first graph. We can see that these locations are quite small, so it's perfect if you don't want to travel a lot and you still want to see many different breweries.

**THE PERCENTAGE OF ALCOHOL**

In [107]:
#Drop the location with less than 5 beers (to do a beer trip, we need to have different beer to drink!) and beer with less than 20 ratings
df_beer_breweries_flt_abv = df_beer_breweries_clean.groupby('location').filter(lambda x: (len(x) > 5) | (x['nbr_ratings'].sum() + x['nbr_ratings.1'].sum() >= 20)) 

# Plot the average abv of the beers in every location as a scatter plot using plotly 
fig_abv_vs_location = px.scatter(df_beer_breweries_flt_abv, x='location', y='abv', color='location')
fig_abv_vs_location.update_yaxes(range=[0, 25])
fig_abv_vs_location.update_xaxes(tickangle=90, showticklabels=False, showgrid=False)
#fig_abv_vs_location.update_layout(title='Abv of the beers in every location', xaxis_title='Location', height=800, width=1500, yaxis_title='Percentage of alcohol')
fig_abv_vs_location.update_layout(xaxis_title='Location', yaxis_title='Percentage of alcohol')
fig_abv_vs_location.update_traces(showlegend=False)
fig_abv_vs_location.show()



In [90]:
#Sort the dataframe by considering the 10 location with the softest beer
avg_abv_location = df_beer_breweries_flt_abv.groupby('location').abv.describe()
avg_abv_location.sort_values(by='mean', ascending=True, inplace=True)
avg_abv_location.reset_index(inplace=True)

#Create a list of the top 10 countries with the most rare beers, but we restrein the list to 2 location from the US
count=0
top_ten_abv_soft = []
for location in avg_abv_location.location:
    if  "United States" in location and count < 2: 
        top_ten_abv_soft.append(location)
        count+=1
    elif "United States" not in location:
        top_ten_abv_soft.append(location)

    if len(top_ten_abv_soft) == 10:
        break


#Create a dataframe with the top 10 countries with the most rare beers for ploting 
df_top_ten_abv_soft = avg_abv_location[avg_abv_location.location.isin(top_ten_abv_soft)]

#Plot the density of breweries per km2 using plotly
fig_top10_abv_soft = px.bar(df_top_ten_abv_soft, x='location', y='mean', color='location')
fig_top10_abv_soft.update_layout(yaxis_title='Average percentage of alcohol')
fig_top10_abv_soft.update_xaxes(title='Location')
fig_top10_abv_soft.update_layout(showlegend=False)
#fig_top10_abv_soft.update_layout(title='Location with the softest beer', yaxis_title='Average percentage of alcohol')
fig_top10_abv_soft.show()

# Export html file for the website 
pyo.plot(fig_top10_abv_soft, filename='top10_abv_soft.html', auto_open=False)


'top10_abv_soft.html'

This ranking is quite original! If you can't handle drinking a lot, but still like to taste a lot of different flavours, these regions are perfect for you. In fact, we've made sure to keep places with a good variety of beers, at least 5 beers per country, and which have been rated at least 20 times in total on both sites. You'll be able to drink, drink, drink without ever getting a headache!

In [91]:
#Sort the dataframe by considering the 10 location with the strongest beer
avg_abv_location = df_beer_breweries_flt_abv.groupby('location').abv.describe()
avg_abv_location.sort_values(by='mean', ascending=False, inplace=True)
avg_abv_location.reset_index(inplace=True)

#Create a list of the top 10 countries with the most rare beers, but we restrein the list to 2 location from the US
count=0
top_ten_abv_strong = []
for location in avg_abv_location.location:
    if  "United States" in location and count < 2: 
        top_ten_abv_strong.append(location)
        count+=1
    elif "United States" not in location:
        top_ten_abv_strong.append(location)

    if len(top_ten_abv_strong) == 10:
        break

#Create a dataframe with the top 10 countries with the most rare beers for ploting 
df_top_ten_abv_strong = avg_abv_location[avg_abv_location.location.isin(top_ten_abv_strong)]

#Plot the density of breweries per km2 using plotly
fig_top10_abv_strong = px.bar(df_top_ten_abv_strong, x='location', y='mean', color='location')
#fig_top10_abv_strong.update_layout(title='Location with the strongest beer', yaxis_title='Average percentage of alcohol')
fig_top10_abv_strong.update_layout(yaxis_title='Average percentage of alcohol', xaxis_title='Location')
fig_top10_abv_strong.update_traces(showlegend=False)
fig_top10_abv_strong.show()


# Export html file for the website 
pyo.plot(fig_top10_abv_strong, filename='top10_abv_strong.html', auto_open=False)



'top10_abv_strong.html'

Here, it's the other way around: you have to be brave to embark on this journey. The beers you'll be drinking are monstrous! Fasten your seatbelts, and take a good bottle of water with you, as it might come in handy if you overindulge. However, we remind you that alcohol abuse is dangerous for your health, so stay reasonable! It's worth noting that the destinations for this trip are very varied around the world, which tells you that people all over the world appreciate strong beers!

**THE RATINGS IN GLOBAL**

In [93]:
#Select only the beers with at least 5 ratings on either sites (RateBeer and Beer Advocate), because we want to have a good idea of the quality of the beers: 
df_beer_breweries_clean_5_plus = df_beer_breweries_clean[(df_beer_breweries_clean['nbr_ratings'] >=5) | (df_beer_breweries_clean['nbr_ratings.1'] >=5)]

#Grouped the beers by location and count the number of beers in each location
df_beer_breweries_clean_5_plus_4plot = df_beer_breweries_clean_5_plus.groupby('location').beer_name.count()

#Plot the location with the most beers with at least 5 ratings on each sites wiht location name on the x axis and from to bigger to the lower using plotly

index = df_beer_breweries_clean_5_plus_4plot.sort_values(ascending=False).index
beers = df_beer_breweries_clean_5_plus_4plot.sort_values(ascending=False)

fig_beers_5_plus = px.bar(df_beer_breweries_clean_5_plus_4plot, x=index, y=beers, color=index) 
#fig_beers_5_plus.update_layout(title='Location with the most beers with at least 5 ratings on each sites', yaxis_title='Number of beers', height=800, width=1200, margin=dict(t=100))
fig_beers_5_plus.update_layout(yaxis_title='Number of beers', height=800, width=1200, margin=dict(t=100))
fig_beers_5_plus.update_xaxes(tickangle=90, showticklabels=False, showgrid=False, title='')
fig_beers_5_plus.update_traces(showlegend=False)
fig_beers_5_plus.show()




We can see on the previous graph that we still have a lot of location to visit after keeping only the beers with more than 5 ratings on both websites, but we can restrain even more this number by imposing conditions on the minimum amount of beers in a location to be considered as a potential destination for the trip. 

In [94]:
#Drop the beers with no zscore in either sites
df_beer_breweries_clean_5_plus = df_beer_breweries_clean_5_plus.drop(df_beer_breweries_clean_5_plus[(df_beer_breweries_clean_5_plus['zscore'].isna()) | (df_beer_breweries_clean_5_plus['zscore.1'].isna())].index)

#Drop the location with less than 5 different beers (to do a beer trip, we need to have different beer to drink!)
df_beer_breweries_flt = df_beer_breweries_clean_5_plus.groupby('location').filter(lambda x: len(x) >= 5)

#Plot the location with more than 5 beers produced and with at least 5 ratings on each sites
df_beer_breweries_flt_4plot = df_beer_breweries_flt.groupby('location').beer_name.count()
print(df_beer_breweries_flt_4plot.shape)

index = df_beer_breweries_flt_4plot.sort_values(ascending=False).index
beers = df_beer_breweries_flt_4plot.sort_values(ascending=False)

fig_beers_5_plus_flt = px.bar(df_beer_breweries_clean_5_plus_4plot, x=index, y=beers, color=index) 
#fig_beers_5_plus_flt.update_layout(title='Location with the most beers with at least 5 ratings on each sites', xaxis_title='location', yaxis_title='Number of beers', height=800, width=1200, margin=dict(t=100))
fig_beers_5_plus_flt.update_layout(xaxis_title='Location', yaxis_title='Number of beers')
fig_beers_5_plus_flt.update_xaxes(showticklabels=False, showgrid=False)
fig_beers_5_plus_flt.update_traces(showlegend=False)
fig_beers_5_plus_flt.show()

# Export html file for the website
pyo.plot(fig_beers_5_plus, filename='global_ratings_beers_5_plus.html', auto_open=False)


(112,)


'global_ratings_beers_5_plus.html'

We still have 95 destinations for our trip. It is a good number to start with! Now lets analysis the data relatively to the ratings and the best way is to analyse the zscore of the beers. Indeed, the z-score basically makes the ratings comparable both across websites and time in general. However, in order to have a representative overall zscore, we will average the ones from BeerAdvocate and Rate Beer by taking into account their amount of ratings, because, as shown in the intro, the reviews are not equally distributed in both sites.  

In [95]:
#Compute the beers'average rating on the two website by creating new columns
df_beer_breweries_flt['total_rating'] = df_beer_breweries_flt['nbr_ratings'] + df_beer_breweries_flt['nbr_ratings.1']
df_beer_breweries_flt['zscore_common'] = df_beer_breweries_flt['nbr_ratings']/df_beer_breweries_flt['total_rating'] * df_beer_breweries_flt['zscore'] + df_beer_breweries_flt['nbr_ratings.1'] / df_beer_breweries_flt['total_rating'] * df_beer_breweries_flt['zscore.1']

# Plot the average rating of the beers in every location as a scatter plot using plotly
fig_avg_rating_vs_location = px.scatter(df_beer_breweries_flt, x='location', y='zscore_common', color='location')
fig_avg_rating_vs_location.update_yaxes(range=[-5, 5])
fig_avg_rating_vs_location.update_xaxes(tickangle=90, showticklabels=False, showgrid=False)
#fig_avg_rating_vs_location.update_layout(title='Average rating of the beers in every location', xaxis_title='Location', height=800, width=1200, yaxis_title='Average rating')
fig_avg_rating_vs_location.update_layout(xaxis_title='Location', yaxis_title='Average rating')
fig_avg_rating_vs_location.update_traces(showlegend=False)
fig_avg_rating_vs_location.show()

# Export html file for the website
pyo.plot(fig_avg_rating_vs_location, filename='avg_rating_vs_location.html', auto_open=False)

#Sort the dataframe by considering the 10 location with the best average rating
avg_rating_location = df_beer_breweries_flt.groupby('location').zscore_common.describe()
avg_rating_location.sort_values(by='mean', ascending=False, inplace=True)
avg_rating_location.reset_index(inplace=True)

#Create a list of the top 10 countries with the most rare beers, but we restrein the list to 2 location from the US
count=0
top_ten_best = []
for location in avg_rating_location.location:
    if  "United States" in location and count < 2: 
        top_ten_best.append(location)
        count+=1
    elif "United States" not in location:
        top_ten_best.append(location)

    if len(top_ten_best) == 10:
        break

#Create a dataframe with the top 10 countries with the most rare beers for ploting 
df_top_ten_best = avg_rating_location[avg_rating_location.location.isin(top_ten_best)]

#To plot the result we need non-negative value, thus we shift the means by the smallest value
df_top_ten_best['mean'] = df_top_ten_best['mean'] - df_top_ten_best['mean'].min()

#Plot the result with stndard deviation as error bar using plotly
fig_top10_best = px.bar(df_top_ten_best, x='location', y='mean', color='location', error_y='std')
#fig_top10_best.update_layout(title='Locations with the best average rating', yaxis_title='Average rating')
fig_top10_best.update_layout(yaxis_title='Average rating', xaxis_title='Location')
fig_top10_best.update_traces(showlegend=False)
fig_top10_best.show()

# Export html file for the website
pyo.plot(fig_top10_best, filename='top10_best_rating.html', auto_open=False)



C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\1173893890.py:39: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



'top10_best_rating.html'

We notice that beers from the USA are rated slightly higher than those from elsewhere. It's easy to see why Americans are a bit chauvinistic, given that both sites come from North America and that most users are from there too. So it made sense not to include more than two US states in each ranking, to reduce this effect.  

If you're a bit new to the scene, this trip is perfect for you. It gives you an insight into what people think about beer, and you'll be going to the top-rated places to taste it. Normally, you won't be disappointed after going to these countries.

However, as we can see on the barplot above, the standard deviation in each location is quite huge. It shows that, in a location, there are well-rated beers, but also some that are badly rated. The precision of this is not good but still gives a good idea of the regions where the overall ratings of the beers are high. The moral is the following: Keep paying attention to what you are drinking, bad beers exist even in those places!


In [96]:
#Sorted the location considering the 10 location with the worst average rating and plot the result
avg_rating_location = df_beer_breweries_flt.groupby('location').zscore_common.describe()
avg_rating_location.sort_values(by='mean', ascending=True, inplace=True)
avg_rating_location.reset_index(inplace=True)

#Create a list of the top 10 countries with the most rare beers, but we restrein the list to 2 location from the US
count=0
top_ten_worst = []
for location in avg_rating_location.location:
    if  "United States" in location and count < 2: 
        top_ten_worst.append(location)
        count+=1
    elif "United States" not in location:
        top_ten_worst.append(location)

    if len(top_ten_worst) == 10:
        break

#Create a dataframe with the top 10 countries with the most rare beers for ploting 
df_top_ten_worst = avg_rating_location[avg_rating_location.location.isin(top_ten_worst)]

#To plot the result we need non-negative value, thus we flip the means which means that the bigger value on the map will be the worst average rating
df_top_ten_worst['mean'] = df_top_ten_worst['mean'] * (-1)



#Plot the result with stndard deviation as error bar with plotly
fig_top10_worst = px.bar(df_top_ten_worst, x='location', y='mean', color='location', error_y='std')
#fig_top10_worst.update_layout(title='Locations with the worst average rating', yaxis_title='Average rating') #----> we remove the title because it's nicer to add them directly in the website
fig_top10_worst.update_layout(yaxis_title='Average rating', xaxis_title='Location') 
fig_top10_worst.update_traces(showlegend=False)
fig_top10_worst.show()

# Export html file for the website
pyo.plot(fig_top10_worst, filename='top10_worst_rating.html', auto_open=False)


C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\947902247.py:23: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



'top10_worst_rating.html'

Mmmmh okay, a bit weird to go on a beer trip to test the worst-rated beer, but why not! Maybe you don't really care about beer and you just want to travel in hot and sunny locations (except for the Faroe Islands of course), if so this trip will be perfect for you! You will drink a cocktail instead of a beer on the beach, which fits well with the vibe too.

WARNING: The mean zscore values have been flipped to be plotted on the world map, so what’s actually displayed on this ranking is (–1* the average zscore)


**THE NUMBER OF USERS PER CAPITA**

In [97]:
#To determine the locations where the population is the most passionate by beer. 
#We thought about computing the amount of reviewers per location relatively to the population of the location.

# Group the users by location and count the number of users in each location
df_users_pop_count_4graph = df_users_pop.groupby('location').user_id.count()

# Get the values of the population in each location 
df_users_pop_4graph = df_users_pop.groupby('location').population.mean()

# Plot the number of users per location using plotly
fig_users_vs_location = px.scatter(df_users_pop_count_4graph, x=df_users_pop_4graph, y=df_users_pop_count_4graph, color=df_users_pop_4graph.index)
#fig_users_vs_location.update_layout(title='Number of users per location', xaxis_title='Population', xaxis_type='log', yaxis_title='Number of users', height=800, width=1200) #----> we remove the title because it's nicer to add them directly in the website
fig_users_vs_location.update_layout(xaxis_title='Population', xaxis_type='log', yaxis_title='Number of users')
fig_users_vs_location.update_traces(showlegend=False)
fig_users_vs_location.show()

# Export html file for the website
pyo.plot(fig_users_vs_location, filename='nbr_users_vs_population.html', auto_open=False)

#_____________________

# Concatenate the two dataframe to have access to users count per location and the respective population
df_users_pop_count = pd.concat([df_users_pop_count_4graph, df_users_pop_4graph], axis=1)
df_users_pop_count['users_per_capita'] = df_users_pop_count['user_id'] / df_users_pop_count['population']
df_users_pop_count.reset_index(inplace=True)
df_users_pop_count.sort_values(by=['users_per_capita'], ascending=False, inplace=True) 

#Create a list of the top 10 countries with the most rare beers, but we restrein the list to 2 location from the US
count=0
top_ten_ratio = []
for location in df_users_pop_count.location:
    if  "United States" in location and count < 2: 
        top_ten_ratio.append(location)
        count+=1
    elif "United States" not in location:
        top_ten_ratio.append(location)

    if len(top_ten_ratio) == 10:
        break

#Create a dataframe with the top 10 countries with the most rare beers for ploting 
df_top_ten_ratio = df_users_pop_count[df_users_pop_count.location.isin(top_ten_ratio)]

# Plot the number of users per location using plotly
fig_top10_ratio = px.bar(df_top_ten_ratio, x='location', y='users_per_capita', color='location')
fig_top10_ratio.update_layout(yaxis_title='Users per capita')
#fig_top10_ratio.update_layout(title='Locations with the most users per capita', yaxis_title='Users per capita')
fig_top10_ratio.update_traces(showlegend=False)
fig_top10_ratio.show()

# Export html file for the website
pyo.plot(fig_top10_ratio, filename='top10_user_capita.html', auto_open=False)



'top10_user_capita.html'

The first graph shows the number of users who review in each location as a function of the population of the region in question. This graph is relevant for illustrating the diversity of user numbers. What's more, the potential locations we'll be taking you to range from tiny, sparsely populated islands (e.g. Faroe Islands) to the most populous regions in the world (e.g. China or India).

If you chose this trip, that means you are very social and you love sharing your experience! You are looking forward to meeting beer experts and that's actually cool, all the BTA team agreed with you (we are the same)! It's so pleasant having a chat on a terrace over a good IPA with a random person who shares the same passion as you!

**THE CONNOISSEUR WORLD TOUR**

Exceptionally in this trip, we're going to use the data specific to each site, as we want to focus on the top 1% of reviewers, who have made the most ratings. Indeed, we assume that people who review a lot have relevant opinions because they have experience in the field of beer tasting, even if they review only on one website and not on both. 

We will attribute points between 1 and 100 according to the z-score ranking of beers. Because Rate Beer and Beer Advocate do not always have the same beer_id fot the same beers (neither the same beer_name) or the same brewery_id for the same brewery we will first sum the points of each beer distilled in the same brewery and then sum the points of each brewery located in the same region/country. This will give us the best countries to visit to get to the best breweries and best beers. 

In [98]:
df_filtered_beer_RB_zscore_sorted = df_filtered_beer_RB_zscore_sorted.head(100)
df_filtered_beer_BA_zscore_sorted = df_filtered_beer_BA_zscore_sorted.head(100)

# Add 'points' column to df_beer_breweries_RB_zscore_sorted
df_filtered_beer_RB_zscore_sorted['points'] = range(100, 0, -1)
# Add 'points' column to df_beer_breweries_BA_zscore_sorted
df_filtered_beer_BA_zscore_sorted['points'] = range(100, 0, -1)

# Merge both data frame with the corresponding breweries data frame to get the locations
df_beer_breweries_BA_zscore_sorted = pd.merge(df_filtered_beer_BA_zscore_sorted, df_breweries_BA, left_on='brewery_id', right_on='id', how='left')
df_beer_breweries_RB_zscore_sorted = pd.merge(df_filtered_beer_RB_zscore_sorted, df_breweries_RB, left_on='brewery_id', right_on='id', how='left')

# Sum the beer points which are distilled by the same brewery. 
df_grouped_BA = df_beer_breweries_BA_zscore_sorted.groupby('brewery_name').agg({'location': 'first', 'points': 'sum'}).reset_index()
df_grouped_RB = df_beer_breweries_RB_zscore_sorted.groupby('brewery_name').agg({'location': 'first', 'points': 'sum'}).reset_index()

In [99]:
# Merging DataFrames on 'brewery_name'
merged_df = pd.merge(df_grouped_RB, df_grouped_BA, on='brewery_name', how='outer')

# Combining 'location_x' and 'location_y' into a new 'location' column
merged_df['location'] = merged_df['location_x'].combine_first(merged_df['location_y'])

# Creating the 'points' column by summing 'points_x' and 'points_y'
merged_df['points'] = merged_df['points_x'].fillna(0) + merged_df['points_y'].fillna(0)

# Dropping unnecessary columns
merged_df.drop(['points_x', 'points_y', 'location_x', 'location_y'], axis=1, inplace=True)

# Sorting the DataFrame by 'points' in descending order
merged_df = merged_df.sort_values('points', ascending=False)



In [100]:
# Group by points per countries and sort by points
sum_points_by_location = merged_df.groupby('location')['points'].sum()
sum_points_by_location = pd.DataFrame(sum_points_by_location)
sum_points_by_location.reset_index(inplace=True)  
sum_points_by_location.sort_values(by='points', ascending=False, inplace=True)

# Create a list of the top 10 countries with the most rare beers, but we restrict the list to 2 locations from the US
count = 0
top_ten_countries = []
for location in sum_points_by_location['location']:
    if "United States" in location and count < 2: 
        top_ten_countries.append(location)
        count += 1
    elif "United States" not in location:
        top_ten_countries.append(location)

    if len(top_ten_countries) == 10:
        break

# Define a list of colors for each bar
colors = ['light blue', 'red', 'green', 'orange', 'purple', 'yellow', 'pink', 'brown', 'gray', 'cyan']

# Create a bar chart for the merged_df dataframe with different colors for each bar
data = [go.Bar(x=top_ten_countries, y=sum_points_by_location.loc[sum_points_by_location['location'].isin(top_ten_countries), 'points'], marker=dict(color=colors))]
#layout = go.Layout(title='Points per countries', xaxis=dict(title='Countries'), yaxis=dict(title='Points'))
layout = go.Layout(xaxis=dict(title='Location'), yaxis=dict(title='Points'))

fig = go.Figure(data=data, layout=layout)
fig.show()

# Save the plot as an HTML file
pyo.plot(fig, filename='connoisseur_fig_top_10.html', auto_open=False)


'connoisseur_fig_top_10.html'

You're an expert, aren't you? So it makes sense that you only trust people who also devote a large part of their time to writing complete, structured analyses. However, we can see that the ranking is not very equitable and that the top four locations are ahead by a long way. No need to panic! That's not to say that the others don't have some good beer to try out - you'll just have to look a little harder to find it!

## Calculation of the overall ranking: 

### Compute the overall ranking

In [101]:
#Compute the overall ranking based on the previous rankings and the data story to set the weight values
def overall_ranking(w1, w2, w3, w4, w5, w6, w7, w8, case_num='1') :
    '''
    Plot the overall ranking based on the previous rankings and their respective weights, given by the customer. 
    The weights must be between 0 and 1 and must sum to 1.

    Args :
        w1 : weight of the discovery trip ranking
        w2 : weight of the brewery density ranking
        w3 : weight of the soft beer ranking 
        w4 : weight of the strong beer ranking
        w5 : weight of the best global ratings ranking
        w6 : weight of the users per capita ranking 
        w7 : weight of the connoisseur ranking 
        w8 : weight for the worst global ratings ranking
        case : the case number of the customer
        
    Return : 
        df_overall : dataframe with the overall ranking location

    '''
    # Add the point for each ranking 
    df_discovery_top10 = pd.DataFrame({'location': top_10_discov, 'score' : [10,9,8,7,6,5,4,3,2,1]})
    df_density_top10 = pd.DataFrame({'location': top_ten_density, 'score' : [10,9,8,7,6,5,4,3,2,1]})
    df_softest_abv_top10 = pd.DataFrame({'location': top_ten_abv_soft, 'score' : [10,9,8,7,6,5,4,3,2,1]})
    df_strongest_abv_top10 = pd.DataFrame({'location': top_ten_abv_strong, 'score' : [10,9,8,7,6,5,4,3,2,1]})
    df_bestratings_top10 = pd.DataFrame({'location': top_ten_best, 'score' : [10,9,8,7,6,5,4,3,2,1]})
    df_users_per_capita_top10 = pd.DataFrame({'location': top_ten_ratio, 'score' : [10,9,8,7,6,5,4,3,2,1]})
    df_connoisseur_top10 = pd.DataFrame({'location': top_ten_countries, 'score' : [10,9,8,7,6,5,4,3,2,1]})
    df_worst_top10 = pd.DataFrame({'location': top_ten_worst, 'score' : [10,9,8,7,6,5,4,3,2,1]})

    # Apply the weights to the score
    df_discovery_top10['score'] = df_discovery_top10['score'] * w1
    df_density_top10['score'] = df_density_top10['score'] * w2
    df_softest_abv_top10['score'] = df_softest_abv_top10['score'] * w3
    df_strongest_abv_top10['score'] = df_strongest_abv_top10['score'] * w4
    df_bestratings_top10['score'] = df_bestratings_top10['score'] * w5
    df_users_per_capita_top10['score'] = df_users_per_capita_top10['score'] * w6
    df_connoisseur_top10['score'] = df_connoisseur_top10['score'] * w7
    df_worst_top10['score'] = df_worst_top10['score'] * w8

    # Concatenate the dataframes
    dfs = [df_discovery_top10, df_density_top10, df_softest_abv_top10, df_strongest_abv_top10, df_bestratings_top10, df_users_per_capita_top10, df_connoisseur_top10, df_worst_top10]
    df_overall = pd.concat(dfs, axis=0, ignore_index=True)

    # Group by location and sum the score
    df_overall = df_overall.groupby('location', as_index=False)['score'].sum()

    #Sort the dataframe by score
    df_overall.sort_values(by='score', ascending=False, inplace=True)
    top_10_overall = df_overall.head(10)


    # Plot the overall ranking using plotly
    fig_overall_ranking = px.bar(df_overall.head(10), x='location', y='score', color='location')
    fig_overall_ranking.update_layout(yaxis_title='Score', xaxis_title='Location')
    #fig_overall_ranking.update_layout(title='Overall ranking', yaxis_title='Score',  xaxis_title='Location', showticklabels=False) #----> we remove the title because it's nicer to add them directly in the website
    fig_overall_ranking.update_traces(showlegend=False)
    fig_overall_ranking.show()

    # Export html file for the website
    pyo.plot(fig_overall_ranking, filename=f'overall_ranking{case_num}.html', auto_open=False)

    return top_10_overall


### Find additional useful travel informations: 

Did you really think that the members of the BTA were going to dump you in the four corners of the world without any information? Well, you don't know us! In fact, we've arranged for you to visit the best brewery in each country you'll be travelling to. On top of that, we've also put you in touch with the most active reviewer in each of your destinations, should you have any questions or need advice!

In [102]:
def find_the_guides(top_ten) :
    '''
    Find the user with the most ratings in each location of the top 10 location of the previous rankings.

    Args :
        top_ten : list of the top 10 location of the previous rankings

    Return :
        best_users : list of the user with the most ratings.
    '''
    # Compute the total number of ratings for each user in each website
    df_users_approx['Total ratings'] = df_users_approx['nbr_ratings'] + df_users_approx['nbr_ratings.1']
    df_users_approx_reduced = df_users_approx[['user_id', 'user_name', 'user_name_lower', 'Total ratings', 'location']]

    best_users = []

    # Select the best user in each location
    for location in top_ten : 
        best_user = df_users_approx_reduced[df_users_approx_reduced['location'] == location]
        best_user.sort_values(by=['Total ratings'], ascending=False, inplace=True) 
        best_user['location'] = location
        best_users.append(best_user.iloc[:1])
        
    df_top3 = pd.concat(best_users, axis=0)

    return df_top3

In [103]:
#To determine the breweries we are going to propose to the cusomer, we need to clean a bit the data 
# Compute the zscore_common (by taking zscore from both websites) of beers for each brewery
df_beer_breweries_clean_reduced = df_beer_breweries_clean[['brewery_name', 'location','zscore','zscore.1','nbr_ratings.1', 'nbr_ratings', 'nbr_beers']]
df_beer_breweries_clean_reduced['total_rating'] = df_beer_breweries_clean_reduced['nbr_ratings'] + df_beer_breweries_clean_reduced['nbr_ratings.1']
df_beer_breweries_clean_reduced['zscore_common'] = df_beer_breweries_clean_reduced['nbr_ratings']/df_beer_breweries_clean_reduced['total_rating'] * df_beer_breweries_clean_reduced['zscore'] + df_beer_breweries_clean_reduced['nbr_ratings.1'] / df_beer_breweries_clean_reduced['total_rating'] * df_beer_breweries_clean_reduced['zscore.1']


# Replace the NaN values in the zscore_common column by the zscore column or the zscore.1 column (or delete the row if both are NaN)   
for zscore, zscore1 in df_beer_breweries_clean_reduced[['zscore', 'zscore.1']].itertuples(index=False):
    if np.isnan(zscore) == True  and np.isnan(zscore1) == True :
        df_beer_breweries_clean_reduced.drop(df_beer_breweries_clean_reduced[(df_beer_breweries_clean_reduced['zscore'] == zscore) & (df_beer_breweries_clean_reduced['zscore.1'] == zscore1)].index, inplace=True)
    elif np.isnan(zscore) == True  and np.isnan(zscore1) == False :
        df_beer_breweries_clean_reduced['zscore_common'] = df_beer_breweries_clean_reduced['zscore.1']
    elif np.isnan(zscore) == False  and np.isnan(zscore1) == True :
        df_beer_breweries_clean_reduced['zscore_common'] = df_beer_breweries_clean_reduced['zscore']
    else :
        continue


C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\2147172060.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\2147172060.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\nicol\AppData\Local\Temp\ipykernel_21632\2147172060.py:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pand

In [104]:
def find_the_breweries(top_ten) :
    '''
    Find the brewery with the most beers in each location of the top 10 location of the previous rankings.

    Args :
        top_ten : list of the top 10 location of the previous rankings

    Return :
        best_breweries : list of the brewery with the most beers.
    '''
    
    best_breweries = []


    # Select the best brewery in each location
    for location in top_ten : 
        best_brewery = df_beer_breweries_clean_reduced[df_beer_breweries_clean_reduced['location'] == location]
        zscore_brewery = best_brewery.groupby('brewery_name').zscore_common.apply(lambda x: x.mean())
        count_brewery = best_brewery.groupby('brewery_name').nbr_beers.apply(lambda x: x.sum())
        group_brewery = pd.concat([zscore_brewery, count_brewery], axis=1)
        group_brewery['location'] = location
        group_brewery.reset_index(inplace=True)
        group_brewery.sort_values(by=['zscore_common'], ascending=False, inplace=True) 
        best_breweries.append(group_brewery.iloc[:1])
    
    best_breweries = pd.concat(best_breweries)

    return best_breweries


# Displaying the trips on a world map 

In [105]:
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut
import plotly.graph_objects as go

geolocator = Nominatim(user_agent="beer world tour")

# Defining function to plot our world tour on a interactive map 
def get_lat_lon(location):
    try:
        location = geolocator.geocode(location)
        return location.latitude, location.longitude
    except GeocoderTimedOut:
        return get_lat_lon(location)

def plot_world_tour(df, metric):

    df['latitude'], df['longitude'] = zip(*df['location'].apply(get_lat_lon))

    # Change de latitude and longitude for those country (error in the geolocator): Russia, Germany, Lebanon, Albania, Sweden, Egypt
    df.loc[df['location'] == 'Russia', 'latitude'] = 61.52401
    df.loc[df['location'] == 'Russia', 'longitude'] = 105.318756
    df.loc[df['location'] == 'Germany', 'latitude'] = 51.0834196
    df.loc[df['location'] == 'Germany', 'longitude'] = 10.4234469
    df.loc[df['location'] == 'Lebanon', 'latitude'] = 33.8750629
    df.loc[df['location'] == 'Lebanon', 'longitude'] = 35.843409
    df.loc[df['location'] == 'Albania', 'latitude'] = 41.000028
    df.loc[df['location'] == 'Albania', 'longitude'] = 19.999962
    df.loc[df['location'] == 'Sweden', 'latitude'] = 60.128161
    df.loc[df['location'] == 'Sweden', 'longitude'] = 18.643501
    df.loc[df['location'] == 'Egypt', 'latitude'] = 26.2540493
    df.loc[df['location'] == 'Egypt', 'longitude'] = 29.2675469

    # Plot the locations with given metric the world tour is made with
    fig = px.scatter_geo(df,
                lat="latitude",
                lon="longitude",
                color="location",
                hover_name="location",
                size=metric,
                projection="orthographic")

    # Add lines connecting the locations
    for i in range(len(df) - 1):
        fig.add_trace(
            go.Scattergeo(
                lon = [df.iloc[i]['longitude'], df.iloc[i + 1]['longitude']],
                lat = [df.iloc[i]['latitude'], df.iloc[i + 1]['latitude']],
                mode = 'lines',
                line = dict(width = 2, color = 'blue'),
                 showlegend=False
            )
        )

    fig.show()

    return fig

In [ ]:
#Run this cells only if you want to plot the world tour on a map, they are already on the website

# DISCOVERY TRIP
discovery_trip = plot_world_tour(df_top_10_discov, 'count')
py.write_html(discovery_trip, 'discovery_trip_map.html')

# BREWERIES PER KM2
breweries_per_km2 = plot_world_tour(df_top_ten_density, 'density')
py.write_html(breweries_per_km2, 'breweries_per_km2_map.html')

# THE PERCENTAGE OF ALCOHOL
soft_beers = plot_world_tour(df_top_ten_abv_soft, 'mean')
strong_beers = plot_world_tour(df_top_ten_abv_strong, 'mean')
py.write_html(soft_beers, 'soft_beers_map.html')
py.write_html(strong_beers, 'strong_beers_map.html')

# THE  BEST RATINGS IN GLOBAL
best_ratings_in_global = plot_world_tour(df_top_ten_best, 'mean')
py.write_html(best_ratings_in_global, 'best_ratings_in_global_map.html')

# THE WORST RATINGS IN GLOBAL
worst_ratings_in_global = plot_world_tour(df_top_ten_worst, 'mean')
py.write_html(worst_ratings_in_global, 'worst_ratings_in_global_map.html')

# THE NUMBER OF USERS PER CAPITA
user_per_capita = plot_world_tour(df_top_ten_ratio, 'users_per_capita')
py.write_html(user_per_capita, 'user_per_capita_map.html')

# THE CONNOISSEUR WORLD TOUR 
merged_df_temp = sum_points_by_location[sum_points_by_location['location'].isin(top_ten_countries)]
merged_df_temp['points'] = np.log(merged_df_temp['points'])
connoisseur = plot_world_tour(merged_df_temp, 'points')
py.write_html(connoisseur, 'connoisseur_map.html')



# Creation of two different overall rankings

Here are two practical cases that BTA members may be confronted with in their careers (for example, groups of customers) for which you must find the best beer trip taking into account their various opinions (everyone gives their preferences).

#### Number 1:
We consider the case where we need to build a trip that satisfies the following conditions : The customers want to discover as many rare beer style than people, in a minor way, they want to taste soft beer, so the weights are the following: 
(w1=2, w2=0, w3=1, w4=0, w5=0, w6=2, w7=0, w8=0)

In [ ]:
# Compute the overall ranking based on the 8 previous rankings and the data story describe above
df1_overall_top10 = overall_ranking(2,0,1,0,0,2,0,0, '1')

# Find the guides for the top 10 locations
list_guide1 = find_the_guides(df1_overall_top10.location)
list_guide1.to_html('guides_to_contact1.html')

# Find the breweries for the top 10 locations
list_breweries1 = find_the_breweries(df1_overall_top10.location)
list_breweries1.to_html('breweries_to_visit1.html')

# Plot the world tour with the top 10 locations
world_tour = plot_world_tour(df1_overall_top10, 'score')
py.write_html(world_tour, 'world_tour_overall1_map.html')

### Number 2: 

For this trip we took into consideration the customers opinions: They want to discover many things! So we set the weights as follow:
(w1=0, w2=1, w3=0, w4=1, w5=2, w6=0, w7=2, w8=0)

In [ ]:
# Compute the overall ranking based on the 8 previous rankings and the data story describe above
df2_overall_top10 = overall_ranking(0,1,0,1,2,0,2,0,'2')

# Find the guides for the top 10 locations
list_guide2 = find_the_guides(df1_overall_top10.location)
list_guide2.to_html('guide_to_contact2.html')

# Find the breweries for the top 10 locations
list_breweries2 = find_the_breweries(df1_overall_top10.location)
list_breweries2.to_html('breweries_to_visit2.html')

# Plot the world tour with the top 10 locations
world_tour2 = plot_world_tour(df2_overall_top10, 'score')
py.write_html(world_tour2, 'world_tour_overall2_map.html')